<a href="https://colab.research.google.com/github/Lord-Kanzler/DS-Unit-4-Sprint-3-Deep-Learning/blob/master/module1-rnn-and-lstm/LS_DS_431_RNN_and_LSTM_Assignment_ALEX_KAISER.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

<img align="left" src="https://lever-client-logos.s3.amazonaws.com/864372b1-534c-480e-acd5-9711f850815c-1524247202159.png" width=200>
<br></br>
<br></br>

## *Data Science Unit 4 Sprint 3 Assignment 1*

# Recurrent Neural Networks and Long Short Term Memory (LSTM)

![Monkey at a typewriter](https://upload.wikimedia.org/wikipedia/commons/thumb/3/3c/Chimpanzee_seated_at_typewriter.jpg/603px-Chimpanzee_seated_at_typewriter.jpg)

It is said that [infinite monkeys typing for an infinite amount of time](https://en.wikipedia.org/wiki/Infinite_monkey_theorem) will eventually type, among other things, the complete works of Wiliam Shakespeare. Let's see if we can get there a bit faster, with the power of Recurrent Neural Networks and LSTM.

This text file contains the complete works of Shakespeare: https://www.gutenberg.org/files/100/100-0.txt

Use it as training data for an RNN - you can keep it simple and train character level, and that is suggested as an initial approach.

Then, use that trained RNN to generate Shakespearean-ish text. Your goal - a function that can take, as an argument, the size of text (e.g. number of characters or lines) to generate, and returns generated text of that size.

Note - Shakespeare wrote an awful lot. It's OK, especially initially, to sample/use smaller data and parameters, so you can have a tighter feedback loop when you're trying to get things running. Then, once you've got a proof of concept - start pushing it more!

In [0]:
# TODO - Words, words, mere words, no matter from the heart.

In [0]:
# imports
from tensorflow.keras.callbacks import LambdaCallback
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, LSTM
from tensorflow.keras.optimizers import RMSprop

import pandas as pd
import numpy as np
import random
import requests
import sys
import os

In [6]:
url = 'https://raw.githubusercontent.com/Lord-Kanzler/DS-Unit-4-Sprint-3-Deep-Learning/master/module1-rnn-and-lstm/shakespeare_entire_works.txt'

df = pd.read_fwf(url, names='1', keep_default_na=False, skip_blank_lines=True)
df.head(50)

1
0                                         THE SONNETS
1                                                   1
2          From fairest creatures we desire increase,
3         That thereby beauty’s rose might never die,
4            But as the riper should by time decease,
5              His tender heir might bear his memory:
6       But thou contracted to thine own bright eyes,
7   Feed’st thy light’s flame with self-substantia...
8               Making a famine where abundance lies,
9      Thy self thy foe, to thy sweet self too cruel:
10      Thou that art now the world’s fresh ornament,
11               And only herald to the gaudy spring,
12          Within thine own bud buriest thy content,
13     And, tender churl, mak’st waste in niggarding:
14           Pity the world, or else this glutton be,
15     To eat the world’s due, by the grave and thee.
16                                                  2
17         When forty winters shall besiege thy brow,
18       And dig deep trenches in thy beauty’s field,
19          Thy youth’s proud livery so gazed on now,
20       Will be a tattered weed of small worth held:
21       Then being asked, where all thy beauty lies,
22          Where all the treasure of thy lusty days;
23         To say, within thine own deep sunken eyes,
24   Were an all-eating shame, and thriftless praise.
25    How much more praise deserv’d thy beauty’s use,
26    If thou couldst answer ‘This fair child of mine
27       Shall sum my count, and make my old excuse,’
28            Proving his beauty by succession thine.
29        This were to be new made when thou art old,
30  And see thy blood warm when thou feel’st it cold.
31                                                  3
32  Look in thy glass and tell the face thou viewest,
33     Now is the time that face should form another,
34       Whose fresh repair if now thou not renewest,
35  Thou dost beguile the world, unbless some mother.
36        For where is she so fair whose uneared womb
37             Disdains the tillage of thy husbandry?
38              Or who is he so fond will be the tomb
39                Of his self-love to stop posterity?
40        Thou art thy mother’s glass and she in thee
41          Calls back the lovely April of her prime,
42    So thou through windows of thine age shalt see,
43          Despite of wrinkles this thy golden time.
44             But if thou live remembered not to be,
45         Die single and thine image dies with thee.
46                                                  4
47          Unthrifty loveliness why dost thou spend,
48                 Upon thy self thy beauty’s legacy?
49      Nature’s bequest gives nothing but doth lend,

In [7]:
df.shape

(138904, 1)

In [5]:
df.tail(50)

1
138854  Strike the wise dumb, and teach the fool to sp...
138855        “It shall be sparing, and too full of riot,
138856  Teaching decrepit age to tread the measures;  ...
138857        The staring ruffian shall it keep in quiet,
138858  Pluck down the rich, enrich the poor with trea...
138859            It shall be raging mad, and silly mild,
138860  Make the young old, the old become a child.   ...
138861       “It shall suspect where is no cause of fear,
138862   It shall not fear where it should most mistrust;
138863              It shall be merciful, and too severe,
138864  And most deceiving when it seems most just;   ...
138865  Perverse it shall be, where it shows most toward,
138866         Put fear to valour, courage to the coward.
138867         “It shall be cause of war and dire events,
138868  And set dissension ’twixt the son and sire;   ...
138869            Subject and servile to all discontents,
138870              As dry combustious matter is to fire,
138871      Sith in his prime death doth my love destroy,
138872  They that love best their love shall not enjoy...
138873        By this the boy that by her side lay kill’d
138874           Was melted like a vapour from her sight,
138875   And in his blood that on the ground lay spill’d,
138876  A purple flower sprung up, chequer’d with whit...
138877     Resembling well his pale cheeks, and the blood
138878   Which in round drops upon their whiteness stood.
138879  She bows her head, the new-sprung flower to sm...
138880  Comparing it to her Adonis’ breath;           ...
138881          And says within her bosom it shall dwell,
138882        Since he himself is reft from her by death;
138883     She drops the stalk, and in the breach appears
138884   Green-dropping sap, which she compares to tears.
138885  “Poor flower,” quoth she, “this was thy father...
138886         Sweet issue of a more sweet-smelling sire,
138887            For every little grief to wet his eyes,
138888  To grow unto himself was his desire,          ...
138889         And so ’tis thine; but know, it is as good
138890            To wither in my breast as in his blood.
138891     “Here was thy father’s bed, here in my breast;
138892  Thou art the next of blood, and ’tis thy right...
138893            Lo in this hollow cradle take thy rest,
138894  My throbbing heart shall rock thee day and night:
138895           There shall not be one minute in an hour
138896   Wherein I will not kiss my sweet love’s flower.”
138897  Thus weary of the world, away she hies,       ...
138898     And yokes her silver doves; by whose swift aid
138899    Their mistress mounted through the empty skies,
138900  In her light chariot quickly is convey’d;     ...
138901  Holding their course to Paphos, where their queen
138902           Means to immure herself and not be seen.
138903                                              FINIS

In [8]:
request = requests.get(url)
request.text

'\ufeff\r\n\r\nTHE SONNETS\r\n\r\n                    1\r\n\r\nFrom fairest creatures we desire increase,\r\nThat thereby beauty’s rose might never die,\r\nBut as the riper should by time decease,\r\nHis tender heir might bear his memory:\r\nBut thou contracted to thine own bright eyes,\r\nFeed’st thy light’s flame with self-substantial fuel,\r\nMaking a famine where abundance lies,\r\nThy self thy foe, to thy sweet self too cruel:\r\nThou that art now the world’s fresh ornament,\r\nAnd only herald to the gaudy spring,\r\nWithin thine own bud buriest thy content,\r\nAnd, tender churl, mak’st waste in niggarding:\r\n  Pity the world, or else this glutton be,\r\n  To eat the world’s due, by the grave and thee.\r\n\r\n\r\n                    2\r\n\r\nWhen forty winters shall besiege thy brow,\r\nAnd dig deep trenches in thy beauty’s field,\r\nThy youth’s proud livery so gazed on now,\r\nWill be a tattered weed of small worth held:\r\nThen being asked, where all thy beauty lies,\r\nWhere a

In [9]:
type(request.text)

str

In [10]:
len(request.text)

5715639

I know JC recommended to use "requests" to obtain the package, and generally that would be a good go-to-method, but in this case "pd.read_fwf" provides a much cleaner source data that's easier to work with in df format.

In [11]:
df['1'][10]

'Thou that art now the world’s fresh ornament,'

In [12]:
# Read in df

data = df['1'].tolist()
len(data)

138904

In [13]:
data[-2]

'Means to immure herself and not be seen.'

In [0]:
# Encode Data as Chars

# Gather all text 
# Why? 1. See all possible characters 2. For training / splitting later
text = " ".join(data)
 
# Unique Characters
chars = list(set(text))

# Lookup Tables
char_int = {c:i for i, c in enumerate(chars)} 
int_char = {i:c for i, c in enumerate(chars)} 

In [15]:
len(chars)

99

In [16]:
# Create the sequence data

maxlen = 40 #was 80
step = 1

encoded = [char_int[c] for c in text]

sequences = [] # Each element is 80 chars long
next_char = [] # One element for each sequence

for i in range(0, len(encoded) - maxlen, step):
    
    sequences.append(encoded[i : i + maxlen])
    next_char.append(encoded[i + maxlen])
    
print('sequences: ', len(sequences))


sequences:  5134682


In [17]:
sequences[0]

[49,
 92,
 16,
 1,
 9,
 35,
 17,
 17,
 16,
 49,
 9,
 1,
 72,
 1,
 71,
 6,
 48,
 67,
 1,
 4,
 47,
 44,
 6,
 41,
 70,
 64,
 1,
 76,
 6,
 41,
 47,
 64,
 78,
 6,
 41,
 70,
 1,
 51,
 41,
 1]

In [19]:
sequences = sequences[:1000000]
print('sequences: ', len(sequences))

sequences:  1000000


In [0]:
# Create x & y

x = np.zeros((len(sequences), maxlen, len(chars)), dtype=np.bool)
y = np.zeros((len(sequences),len(chars)), dtype=np.bool)

for i, sequence in enumerate(sequences):
    for t, char in enumerate(sequence):
        x[i,t,char] = 1
        
    y[i, next_char[i]] = 1

In [0]:
# # causing a Colab Crash so I can increase RAM
# a = []
# while(1):
#     a.append('1')

In [21]:
x.shape

(1000000, 40, 99)

In [22]:
y.shape

(1000000, 99)

In [0]:
# build the model: a single LSTM

model = Sequential()
model.add(LSTM(128, input_shape=(maxlen, len(chars)), activation='tanh', recurrent_activation='sigmoid', dropout=0.2, recurrent_dropout=0, unroll=False, use_bias=True))
model.add(Dense(len(chars), activation='softmax'))

model.compile(loss='categorical_crossentropy', optimizer='adam')

In [0]:
def sample(preds):
    # helper function to sample an index from a probability array
    preds = np.asarray(preds).astype('float64')
    preds = np.log(preds) / 1
    exp_preds = np.exp(preds)
    preds = exp_preds / np.sum(exp_preds)
    probas = np.random.multinomial(1, preds, 1)
    return np.argmax(probas)

In [0]:
def on_epoch_end(epoch, _):
    # Function invoked at end of each epoch. Prints generated text.
    
    print()
    print('----- Generating text after Epoch: %d' % epoch)
    
    start_index = random.randint(0, len(text) - maxlen - 1)
    
    generated = ''
    
    sentence = text[start_index: start_index + maxlen]
    generated += sentence
    
    print('----- Generating with seed: "' + sentence + '"')
    sys.stdout.write(generated)
    
    for i in range(400):
        x_pred = np.zeros((1, maxlen, len(chars)))
        for t, char in enumerate(sentence):
            x_pred[0, t, char_int[char]] = 1
            
        preds = model.predict(x_pred, verbose=0)[0]
        next_index = sample(preds)
        next_char = int_char[next_index]
        
        sentence = sentence[1:] + next_char
        
        sys.stdout.write(next_char)
        sys.stdout.flush()
    print()


print_callback = LambdaCallback(on_epoch_end=on_epoch_end)

In [29]:
# fit the model

model.fit(x, y,
          batch_size=512,
          epochs=100,
          callbacks=[print_callback])

Epoch 1/100
1953/1954 [============================>.] - ETA: 0s - loss: 2.3108
----- Generating text after Epoch: 0
----- Generating with seed: "hter, speak you: He cares not for your w"
hter, speak you: He cares not for your will keominesyatdy oamalegr swan, As nat ich pabete'm jaitiliin of hom geat leca as o ir hin, Lut apuswy dimint. OCATIN. Hemea hise somma teans nires at the basenus not I me queeg. You ha ran, Nor Ahit bet tomst am'rostjudd bruthins fausthie to kay’llgd alldnospusse ICLENILUS. To host, Rot whin we to nut reat efer Ford; If ardsond ow is ent A Foun me uake; the ardse’slw! Thatye foieng you yo, uree 
1954/1954 [==============================] - 29s 15ms/step - loss: 2.3108
Epoch 2/100
1954/1954 [==============================] - ETA: 0s - loss: 2.2150
----- Generating text after Epoch: 1
----- Generating with seed: "WIS. Queen Margaret, Prince Edward, and "
WIS. Queen Margaret, Prince Edward, and bur Ran with he jasus no as Shenwerd, And atronguntmeafirerturue. Car

# Resources and Stretch Goals

## Stretch goals:
- Refine the training and generation of text to be able to ask for different genres/styles of Shakespearean text (e.g. plays versus sonnets)
- Train a classification model that takes text and returns which work of Shakespeare it is most likely to be from
- Make it more performant! Many possible routes here - lean on Keras, optimize the code, and/or use more resources (AWS, etc.)
- Revisit the news example from class, and improve it - use categories or tags to refine the model/generation, or train a news classifier
- Run on bigger, better data

## Resources:
- [The Unreasonable Effectiveness of Recurrent Neural Networks](https://karpathy.github.io/2015/05/21/rnn-effectiveness/) - a seminal writeup demonstrating a simple but effective character-level NLP RNN
- [Simple NumPy implementation of RNN](https://github.com/JY-Yoon/RNN-Implementation-using-NumPy/blob/master/RNN%20Implementation%20using%20NumPy.ipynb) - Python 3 version of the code from "Unreasonable Effectiveness"
- [TensorFlow RNN Tutorial](https://github.com/tensorflow/models/tree/master/tutorials/rnn) - code for training a RNN on the Penn Tree Bank language dataset
- [4 part tutorial on RNN](http://www.wildml.com/2015/09/recurrent-neural-networks-tutorial-part-1-introduction-to-rnns/) - relates RNN to the vanishing gradient problem, and provides example implementation
- [RNN training tips and tricks](https://github.com/karpathy/char-rnn#tips-and-tricks) - some rules of thumb for parameterizing and training your RNN